# Statistical analysis of calibration factors#

Author: Mikhail Karnevskiy, Version 0.2

Plot calibration constants retrieved from the cal. DB.

To be visualized, calibration constants are averaged per group of pixels. Plots shows calibration constant over time for each constant.

Values shown in plots are saved in h5 files.

In [ ]:
out_folder = "/gpfs/exfel/data/scratch/karnem/test_bla4/"  # Output folder, required
use_existing = "/home/karnem/myscratch/PlotCalDB/SPB/AGIPD1M1/" # Input folder
dclass = "AGIPD"  # Detector class
nMemToShow = 32 # Number of memory cells to be shown in plots over ASICs
range_offset = [4000., 5500, 6500, 8500] # plotting range for offset: high gain l, r, medium gain l, r 
range_noise = [2.5, 15, 7.5, 17.0] # plotting range for noise: high gain l, r, medium gain l, r 
range_gain = [0.8, 1.2, 0.8, 1.2] # plotting range for gain: high gain l, r, medium gain l, r 
range_noise_e = [85., 500., 85., 500.] # plotting range for noise in [e-]: high gain l, r, medium gain l, r 
range_slopesPC = [22.0, 27.0, -0.5, 1.5] # plotting range for slope PC: high gain l, r, medium gain l, r 
range_slopesCI = [22.0, 27.0, -0.5, 1.5] # plotting range for slope CI: high gain l, r, medium gain l, r 
range_slopesFF = [0.8, 1.2, 0.6, 1.2] # plotting range for slope FF: high gain l, r, medium gain l, r 
plot_range = 3 # range for plotting in units of median absolute deviations
x_labels = ['Sensor Bias Voltage', 'Memory cells'] # parameters to be shown on X axis
spShape = [64, 64] # Shape of superpixel
gain_titles = ['High gain', 'Medium gain', 'Low gain'] # Title inset related to gain

In [ ]:
import warnings

warnings.filterwarnings('ignore')
import numpy as np
from cal_tools.ana_tools import (
    HMType,
    IMType,
    get_range,
    hm_combine,
    load_data_from_hdf5,
    multi_union,
)

In [ ]:
if use_existing == '':
    use_existing = out_folder

In [ ]:
print('Load data from {}/CalDBAna_{}_*.h5'.format(use_existing, dclass))
ret_constants = load_data_from_hdf5(
    '{}/CalDBAna_{}_*.h5'.format(use_existing, dclass))

print('Evaluated data from {}/CalDBAna_{}_Gain*.h5'.format(out_folder, dclass))
ret_constants.update(load_data_from_hdf5(
    '{}/CalDBAna_{}_Gain*.h5'.format(out_folder, dclass)))

In [ ]:
# Parameters for plotting

# Define range for plotting
rangevals = {
    "Offset": [range_offset[0:2], range_offset[2:4]],
    "Noise": [range_noise[0:2], range_noise[2:4]],
    "Gain": [range_gain[0:2], range_gain[2:4]],
    "Noise-e": [range_noise_e[0:2], range_noise_e[2:4]],
    "SlopesPC": [range_slopesPC[0:2], range_slopesPC[2:4]],
    "SlopesCI": [range_slopesCI[0:2], range_slopesCI[2:4]],
    "SlopesFF": [range_slopesFF[0:2], range_slopesFF[2:4]]
}

keys = {
    'Mean': ['data', '', 'Mean over pixels'],
    'std': ['dataStd', '', '$\sigma$ over pixels'],
    'MeanBP': ['dataBP', 'Good pixels only', 'Mean over pixels'],
    'NBP': ['nBP', '', 'Fraction of BP'],
    'stdBP': ['dataBPStd', 'Good pixels only', '$\sigma$ over pixels'],
    'stdASIC': ['', '', '$\sigma$ over ASICs'],
    'stdCell': ['', '', '$\sigma$ over Cells'],
}

In [ ]:
print('Plot calibration constants')

# loop over constat type
for const, modules in ret_constants.items():

    const = const.split("_")
    gain = [int(x[1]) for x in const if 'g' in x]
    gain = gain[0] if len(gain)>0 else None
    print('Const: {}, gain {}'.format(const, gain))

    # loop over modules
    mod_data = {}
    mod_data['stdASIC'] = []
    mod_data['stdCell'] = []
    mod_names = []
    mod_times = []

    # Loop over modules
    for mod, data in modules.items():
        ctimes = np.array(data["ctime"])
        ctimes_ticks = [x.strftime('%y-%m-%d') for x in ctimes]

        if ("mdata" in data):
            cmdata = np.array(data["mdata"])
            for i, tick in enumerate(ctimes_ticks):
                for entr in x_labels:
                    key  = entr[0].upper()
                    val = cmdata[i].get(entr, None)
                    if val is not None:
                        ctimes_ticks[i] += ', {}={:.1f}'.format(key, val)

        sort_ind = np.argsort(ctimes_ticks)
        ctimes_ticks = list(np.array(ctimes_ticks)[sort_ind])

        # Create sorted by data dataset
        rdata = {}
        for key, item in keys.items():
            if item[0] in data:
                rdata[key] = np.array(data[item[0]])[sort_ind]

        nTimes = rdata['Mean'].shape[0]
        nPixels = rdata['Mean'].shape[1] * rdata['Mean'].shape[2]
        nBins = nMemToShow * nPixels

        if 'NBP' in rdata:
            rdata["NBP"] = rdata["NBP"] / (spShape[0] * spShape[1]) * 100

        # Reshape: ASICs over cells for plotting
        pdata = {}
        for key in rdata:
            pdata[key] = rdata[key][:, :, :, :nMemToShow].reshape(
                nTimes, nBins).swapaxes(0, 1)

        # Summary information over modules
        for key in pdata:
            if key not in mod_data:
                mod_data[key] = []

            mod_data[key].append(np.nanmean(pdata[key], axis=0))
            # Avoid too low values
            if const[0] in ["Noise", "Offset", "Noise-e"] and key in ['Mean', 'MeanBP']:
                mod_data[key][-1][mod_data[key][-1] == 0.0] = IMType.STRANGE_VAL.value
            if key=='NBP':
                if 'Mean' in mod_data:
                    mod_data['Mean'][-1][mod_data[key][-1] == 100] = IMType.ALL_BAD.value
                if 'MeanBP' in mod_data:
                    mod_data['MeanBP'][-1][mod_data[key][-1] == 100] = IMType.ALL_BAD.value
                mod_data[key][-1][mod_data[key][-1] == 100] = IMType.ALL_BAD.value


        mod_data['stdASIC'].append(np.nanstd(
            np.nanmean(rdata['Mean'][:, :, :, :nMemToShow], axis=(1, 2)), axis=1))
        mod_data['stdCell'].append(np.nanstd(
            np.nanmean(rdata['Mean'][:, :, :, :nMemToShow], axis=3), axis=(1, 2)))

        mod_names.append(mod)
        mod_times.append(ctimes_ticks)

    # Insert nans to get array-like list of data
    uTime = mod_times[0]
    for tlist in mod_times:
        uTime = sorted(multi_union(uTime, tlist))

    for i, tlist in enumerate(mod_times):
        for t, time in enumerate(uTime):
            if t == len(tlist) or time != tlist[t]:
                tlist.insert(t, time)
                for key in mod_data:
                    mod_data[key][i] = np.insert(
                        mod_data[key][i], t, IMType.NO_CONST.value )

    # Plotting
    nModules = len(mod_names)
    mod_idx = np.argsort(mod_names)
    for key in mod_data:
        vmin,vmax = get_range(np.array(mod_data[key])[mod_idx][::-1].flatten(), plot_range)

        htype = None
        if const[0] in ['SlopesFF', 'SlopesPC', 'SlopesCI']:
            htype = HMType.INSET_1D
            
        if key == 'NBP':
            unit = '[%]'
            title = 'BadPixelsDark'
        else:
            unit = '[ADU]'
            title = const[0]

        title += ', All modules'
        if keys[key][1] != '':
            title += ', {}'.format(keys[key][1])
        if gain is not None:
            title += ', {}'.format(gain_titles[gain])
        
        cb_label = '{}, {} {}'.format(const[0], keys[key][2], unit)
        hm_combine(np.array(mod_data[key])[mod_idx][::-1],
                  y_ticks=np.arange(nModules)[::-1]+0.8,
                  y_ticklabels=np.array(mod_names)[mod_idx],
                  x_label='Creation Time', y_label='Module ID',
                  x_ticklabels=ctimes_ticks, x_ticks=np.arange(
                          len(ctimes_ticks))+0.3,
                  title=title, cb_label=cb_label,
                  fname='{}/{}_all_g{}_{}.png'.format(
            out_folder, const[0], gain, key),
            vmin=vmin, vmax=vmax,
            pad=[0.125, 0.151, 0.12, 0.17], htype=htype)